In [28]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
import numpy as np
    
output_notebook()

Loading BokehJS ...

kalmanStates.zip is a compressed .csv (actually, semicolon separated values) file where one of the columns is a timer that increments every at regular intervals depending on the IMU model.  Another column is the heading angle of an IMU ($\psi$). We reduce this dataset by taking every tenth line into a pandas dataframe df.

In [29]:
all_data = pd.read_csv('IMS-2019-10-24-11-31-12-kalmanStates.zip', sep=';', header=0, compression='zip')
#all_data = pd.read_csv('IMS-2019-11-18-15-46-0-kalmanStates.zip', sep=';', header=0, compression='zip')
df = all_data.iloc[::10]

In [30]:
delta_sync = np.diff(df.syncCount)
samplerate = (np.average(delta_sync))
samplerate = np.round(samplerate)
print ("Detected samplerate : {:.0f}ms => 1 second = {} samples".format(samplerate, 1000.0/samplerate))
window_duration = 5  # seconds
windowsize =  int(1000 * window_duration / samplerate)
limit_s = 2.0
print ("Standing means less than {:.1f}m change during {:.0f}s or {:.0f} samples".format(limit_s, window_duration, windowsize))

Detected samplerate : 50ms => 1 second = 20.0 samples
Standing means less than 2.0m change during 5s or 100 samples


The travelled distance column is constant whenever the trolley stops. If during 2.5 seconds the system has moved more than 0.1 meter, we assume IMS is moving.

In [31]:
p=figure(plot_width=950, title="Red = not moving, Green = speed")
delta_s = np.diff(df.distance)
window_standing = windowsize
standing = np.convolve(np.fabs(delta_s), np.ones(window_standing)) < limit_s
standing = standing[window_standing//2-1 : -window_standing//2+1]

speed = delta_s * 1000 / samplerate 
valrange = speed.max() # 0/1 mask scale factor for plotting it with values
masked = p.line(df.syncCount, standing * valrange, color='red', line_width=2, alpha=0.5)

p.line(df.syncCount[:-1], speed, color='green', line_width=2)
show(p)

In [32]:
p=figure(plot_width=950, title="Heading Angle vs. time")
p.line(df.syncCount, df.psi, line_width=2)
show(p)

The heading angle signal shows a sharp drop near clock 1.0e6. At this time the IMU was rotated left by 180 degrees which resulted in a decline of the azimuth angle by $\pi$. This turn took about 200 samples at a 50ms sample period which corresponds to 10 seconds or an angle velocity of pi/10 seconds or 18 degree/sec. There is another steep increase near 6.4e6. This change is less than 180 degree - therefore not an IMU initialization but happening at a similar speed. At the end of the measurement the device was taken off the track before it was switched off. We are interested in the change rate of the angle. Rotating the trolley should result in angle velocities greater than any movements on track. To separate the 2 types of movement we could use an upper bound for angle velocity on-track. Assume a minimum radius of 10m, which is rare (only narrow gauge tram lines), and a high velocity of 3.0m/s. A 180 degree turn would mean an arc length of $10.0 * \pi \approx 31.416m$. Such a distance can be traveled in approximately 10s at our maximum speed. The resulting angle velocity would then be up to $ \frac{\pi}{10} \frac{rad}{s}$ or 18 $\frac{deg}{sec}$, which is not slower than the turning during initialization. Only in combination with the odometer we can be sure what type of rotation we are observing.
Th ususal Railways curves have a Radius above 100m 

We can tell if a trolley is rotating but not rolling by using the previous detection of trolley standing state, combined with a detected angle velocity of more than 12 degree/second

In [33]:
delta_psi = np.diff(df.psi)
limit = np.pi / 15.0
window_turn_samples = int(1000 / samplerate)

print ("One second has : {:.0f} samples. Psi changes more than {:.2f} deg?".format(window_turn_samples, limit*180.0/np.pi))

turning = np.convolve(np.fabs(delta_psi), np.ones(window_turn_samples)) > limit
turning = turning[window_turn_samples//2-1 : -window_turn_samples//2+1]
turn_standing = np.logical_and(turning, standing)

p=figure(plot_width=950, title="Red = turning but not moving on track:")
p.line(df.syncCount,  turning, color = 'blue')
p.line(df.syncCount,  standing, color = 'yellow')
p.line(df.syncCount,  turn_standing, color='red', alpha=0.5, width=8)
show(p)

One second has : 20 samples. Psi changes more than 12.00 deg?
